<small><i>This notebook was put together by [Wesley Beckner](http://wesleybeckner.github.io/).</i></small>

<a id='top'></a>

## 2D descriptor selection

load json parsing [here](#json)

load descriptor generation [here](#descriptors)

check datasets [here](#check)

In [1]:
import json
import os
import sys
import pandas as pd
import numpy as np
from __future__ import print_function

#rdkit modules
from rdkit import Chem
from rdkit.Chem import AllChem
from rdkit.Chem import Descriptors
from rdkit.ML.Descriptors.MoleculeDescriptors import MolecularDescriptorCalculator as Calculator

#pychem modules
import pychem 
from pychem.pychem import PyChem2d, PyChem3d

#scikit modules
from sklearn.linear_model import Lasso
from sklearn.svm import SVR
from sklearn.preprocessing import StandardScaler

#plot modules and formatting
import matplotlib.pyplot as plt
%matplotlib inline
plt.rc("figure", facecolor="white")
params = {
    'lines.markersize' : 10,
    'axes.labelsize': 20,
    'font.size': 20,
    'legend.fontsize': 20,
    'xtick.labelsize': 20,
    'ytick.labelsize': 20,
    'text.usetex': False,
   }
tableau20 = [(31, 119, 180), (174, 199, 232), (255, 127, 14), (255, 187, 120),    
             (44, 160, 44), (152, 223, 138), (214, 39, 40), (255, 152, 150),    
             (148, 103, 189), (197, 176, 213), (140, 86, 75), (196, 156, 148),    
             (227, 119, 194), (247, 182, 210), (127, 127, 127), (199, 199, 199),    
             (188, 189, 34), (219, 219, 141), (23, 190, 207), (158, 218, 229)]   
# Scale the RGB values to the [0, 1] range, which is the format matplotlib accepts.    
for i in range(len(tableau20)):    
    r, g, b = tableau20[i]    
    tableau20[i] = (r / 255., g / 255., b / 255.) 

#grab our checkName code
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
import salty

<a id='json'></a>

# Parse JSON files

[back to top](#top)

In [2]:
###add JSON files to density.csv
outer_old = pd.DataFrame()
outer_new = pd.DataFrame()

for i in range(2266):
    with open("../salty/data/DENSITY/%s.json" % str(i+1)) as json_file:
        
        #grab data, data headers (names), the salt name
        json_full = json.load(json_file)
        json_data = pd.DataFrame(json_full['data'])
        json_datanames = np.array(json_full['dhead'])
        json_data.columns =  json_datanames
        json_saltname = pd.DataFrame(json_full['components'])
        print(json_saltname.iloc[0][3])
        
        inner_old = pd.DataFrame()
        inner_new = pd.DataFrame()
        
        #loop through the columns of the data, note that some of the 
        #json files are missing pressure data. 
        for indexer in range(len(json_data.columns)):
            grab=json_data.columns[indexer]
            list = json_data[grab]
            my_list = [l[0] for l in list]
            dfmy_list = pd.DataFrame(my_list)
            dfmy_list.columns = [json_datanames[indexer][0]]
            inner_new = pd.concat([dfmy_list, inner_old], axis=1)
            inner_old = inner_new
            
        #add the name of the salt    
        inner_old['salt_name']=json_saltname.iloc[0][3]           
        
        #add to the growing dataframe
        outer_new = pd.concat([inner_old, outer_old], axis=0)
        outer_old = outer_new
print(outer_old)
pd.DataFrame.to_csv(outer_old, path_or_buf='../salty/data/density.csv', index=False)

1-hexyl-3-methylimidazolium bis[(trifluoromethyl)sulfonyl]imide
1-butyl-3-methylimidazolium tetrafluoroborate
1-butyl-3-methylimidazolium methylsulfate
1-ethyl-3-methylimidazolium ethyl sulfate
2-hydroxy-N-methylethanaminium pentanoate
2-hydroxy-N-methylethanaminium propionate
N-methyl-2-hydroxyethylammonium acetate
2-hydroxy-N-methylethanaminium formate
2-hydroxy-N-methylethanaminium isobutyrate
N-methyl-2-hydroxyethylammonium butanoate
1-butyl-3-methylimidazolium bis(trifluoromethylsulfonyl)imide
1-ethyl-3-methylimidazolium ethyl sulfate
1-butyl-3-methylimidazolium tetrafluoroborate
1-butyl-3-methylimidazolium hexafluorophosphate
1-hexyl-3-methylimidazolium hexafluorophosphate
1-ethyl-3-methylimidazolium tetrafluoroborate
1-octyl-3-methylimidazolium hexafluorophosphate
1-hexyl-3-methylimidazolium tetrafluoroborate
tetradecyl(trihexyl)phosphonium dicyanamide
1-butyl-3-methylimidazolium bis(trifluoromethylsulfonyl)imide
1-butyl-3-methylimidazolium octyl sulfate
1-butyl-3-methylimidazol

KeyboardInterrupt: 

In [ ]:
###read in the salts csv; add cat_name, an_name, cat_SMILES, and an_SMILES
###columns. Parse salt_name into cation and anion components and append to
###respective columns. Make the call to checkName with those entries and
###append to respective SMILES columns.
salts=pd.read_csv('../salty/data/density.csv',delimiter=',')
salts['cation_name'] = np.nan
salts['anion_name'] = np.nan
salts['cation_SMILES'] = np.nan
salts['anion_SMILES'] = np.nan
for i in range(salts.shape[0]):
    salts.ix[i, 'cation_name'] = salts['salt_name'].iloc[i].split()[0]
    try:
        salts.ix[i, 'cation_SMILES'] = salty.checkName(salts['cation_name'].iloc[i])
    except:
        pass
    if len(salts['salt_name'].iloc[i].split()) == 2:
        salts.ix[i, 'anion_name'] = salts['salt_name'].iloc[i].split()[1]
    elif len(salts['salt_name'].iloc[i].split()) == 1:
        print("only one compound listed")
    else:
        print("long anion name")
        salts.ix[i, 'anion_name'] = (salts['salt_name'].iloc[i].split()[1] + \
        " " + salts['salt_name'].iloc[i].split()[2])
    try:
        salts.ix[i, 'anion_SMILES'] = salty.checkName(salts['anion_name'].iloc[i])
    except:
        pass

query Empty DataFrame
Columns: [Unnamed: 0, cation_SMILES, anion_SMILES, salt_SMILES, cation_name, anion_name, salt_name]
Index: [] not found
user has queried with a name
your query has returned C(#N)[N-]C#N
user has queried with a name
your query has returned CCN1C=C[N+](=C1)C
user has queried with a name
your query has returned C(F)(F)(F)S(=O)(=O)[N-]S(=O)(=O)C(F)(F)F
user has queried with a name
your query has returned CCCCCCCCCCCCCC[P+](CCCCCC)(CCCCCC)CCCCCC
user has queried with a name
your query has returned [Cl-]
query Empty DataFrame
Columns: [Unnamed: 0, cation_SMILES, anion_SMILES, salt_SMILES, cation_name, anion_name, salt_name]
Index: [] not found
query Empty DataFrame
Columns: [Unnamed: 0, cation_SMILES, anion_SMILES, salt_SMILES, cation_name, anion_name, salt_name]
Index: [] not found
query Empty DataFrame
Columns: [Unnamed: 0, cation_SMILES, anion_SMILES, salt_SMILES, cation_name, anion_name, salt_name]
Index: [] not found
user has queried with a name
your query has retu

In [6]:
pd.DataFrame.to_csv(salts, path_or_buf='../salty/data/salts_with_smiles.csv', index=False)

In [7]:
###remove all the salts not found in our database and
###save the truncated salt data
salts=pd.read_csv('../salty/data/salts_with_smiles.csv',delimiter=',')
salts = salts.loc[salts['cation_SMILES'] != "0"]
salts = salts.loc[salts['cation_SMILES'] != "0.0"]
salts = salts.loc[salts['anion_SMILES'] != "0"]
salts = salts.loc[salts['anion_SMILES'] != "0.0"]
salts['salt_SMILES'] = salts['cation_SMILES'] + " " + salts['anion_SMILES']
pd.DataFrame.to_csv(salts, path_or_buf='../salty/data/salts_with_smiles.csv', index=False)

<a id='descriptors'></a>

# Create Descriptors - RDKit version

[back to top](#top)

In [10]:
f = open('../salty/data/Deslist','r')
for line in f:
    print(line)

steiger

Marsili Partial Charges

BalabanJ

BertzCT	

Ipc

HallKierAlpha

Kappa1

Kappa2

Kappa3

Chi0

Chi1

Chi0n

Chi1n

Chi2n

Chi3n

Chi4n

Chi0v

Chi1v

Chi2v

Chi3v

Chi4v

MolLogP

MolMR

MolWt

HeavyAtomCount

HeavyAtomMolWt

NHOHCount

NOCount

NumHAcceptors

NumHDonors

NumHeteroatoms

NumRotatableBonds

NumValenceElectrons

RingCount

TPSA

LabuteASA

PEOE_VSA1

PEOE_VSA2

PEOE_VSA3

PEOE_VSA4

PEOE_VSA5

PEOE_VSA6

PEOE_VSA7

PEOE_VSA8

PEOE_VSA9

PEOE_VSA10

PEOE_VSA11

PEOE_VSA12

PEOE_VSA13

PEOE_VSA14

SMR_VSA1

SMR_VSA2

SMR_VSA3

SMR_VSA4

SMR_VSA5

SMR_VSA6

SMR_VSA7

SMR_VSA8

SMR_VSA9

SMR_VSA10	

SlogP_VSA1

SlogP_VSA2

SlogP_VSA3

SlogP_VSA4

SlogP_VSA5

SlogP_VSA6

SlogP_VSA7

SlogP_VSA8

SlogP_VSA9

SlogP_VSA10

SlogP_VSA11

SlogP_VSA12	

EState_VSA1

EState_VSA2

EState_VSA3

EState_VSA4

EState_VSA5

EState_VSA6

EState_VSA7

EState_VSA8

EState_VSA9

EState_VSA10

EState_VSA11

VSA_EState1

VSA_EState2

VSA_EState3

VSA_EState4

VSA_EState5

VSA_EState6

VS

In [17]:
###based on coco's Deslist
data=pd.read_csv('../salty/data/salts_with_smiles.csv',delimiter=',')
print(data.columns)
n = data.shape[0]
f = open('../salty/data/Deslist','r')
Deslist = []
for line in f:
    Deslist.append(line.strip('\n\t'))
calc = Calculator(Deslist)
D = len(Deslist)
d = len(Deslist)*2+6
print(n,d)

Index([u'Molar volume, m<SUP>3</SUP>/mol', u'Pressure, kPa',
       u'Specific density, kg/m<SUP>3</SUP>',
       u'Specific volume, m<SUP>3</SUP>/kg', u'Temperature, K', u'salt_name',
       u'cation_name', u'anion_name', u'cation_SMILES', u'anion_SMILES',
       u'salt_SMILES'],
      dtype='object')
9172 194


In [12]:
X = np.zeros((n,d))
X[:,-3] = data['Temperature, K']
X[:,-2] = data['Pressure, kPa']
for i in range(n):
    cation = Chem.MolFromSmiles(data['cation_SMILES'][i])
    anion  = Chem.MolFromSmiles(data['anion_SMILES'][i])
    X[i][:D]    = calc.CalcDescriptors(cation)
    X[i][D:2*D] = calc.CalcDescriptors(anion)

X[:,-1] = data['Specific density, kg/m<SUP>3</SUP>']

cols_cat = [s + "-cation" for s in Deslist]
cols_ani = [s + "-anion" for s in Deslist]
cols = cols_cat + cols_ani + ["salt_name" , "NAME_CAT", "NAME_ANI", "Temperature_K" , "Pressure_kPa", "Density_kg/m"]

X = pd.DataFrame(X, columns=cols)
X.iloc[:,-6] = data['salt_name']
X.iloc[:,-5] = data['cation_name']
X.iloc[:,-4] = data['anion_name']

print(X.shape)

# pd.DataFrame.to_csv(X, path_or_buf='../salty/data/salts_with_descriptors.csv', index=False)

(9172, 194)


<a id='descriptors'></a>

# Create Descriptors - Pychem version

[back to top](#top)

In [25]:
datadf = salts.loc[salts["cation_name"].str.contains("ammonium", case=False)]
datadf = datadf.reset_index(drop=True)
datadf

index  Molar volume, m<SUP>3</SUP>/mol  Pressure, kPa  \
0       9                              NaN        101.325   
1      56                              NaN        101.325   
2      59                              NaN        101.325   
3      75                              NaN        101.325   
4      99                              NaN        101.000   
5     103                              NaN        101.325   
6     105                              NaN        101.325   
7    1579                              NaN        100.000   
8    1580                              NaN        100.000   
9    1581                              NaN        100.000   
10   1582                              NaN        100.000   
11   1583                              NaN        100.000   
12   1584                              NaN        100.000   
13   1585                              NaN        100.000   
14   1586                              NaN        100.000   
15   1587                              NaN        100.000   
16   1588                              NaN        100.000   
17   1589                              NaN        100.000   
18   1590                              NaN        100.000   
19   1591                              NaN        100.000   
20   1592                              NaN        100.000   
21   1593                              NaN        100.000   
22   1594                              NaN        100.000   
23   1595                              NaN        100.000   
24   1596                              NaN        100.000   
25   1806                              NaN        101.325   
26   1807                              NaN        101.325   
27   1808                              NaN        101.325   
28   1809                              NaN        101.325   
29   1810                              NaN        101.325   
30   1811                              NaN        101.325   
31   1812                              NaN        101.325   
32   1813                              NaN        101.325   
33   1814                              NaN        101.325   
34   1815                              NaN        101.325   
35   1816                              NaN        101.325   
36   1817                              NaN        101.325   
37   1818                              NaN        101.325   
38   1819                              NaN        101.325   
39   1820                              NaN        101.325   
40   1821                              NaN        101.325   
41   1822                              NaN        101.325   
42   1823                              NaN        101.325   
43   1824                              NaN        101.325   
44   1825                              NaN        101.325   
45   1826                              NaN        101.325   
46   1827                              NaN        101.325   

    Specific density, kg/m<SUP>3</SUP>  Specific volume, m<SUP>3</SUP>/kg  \
0                              1800.00                                NaN   
1                              1840.00                                NaN   
2                              1818.30                                NaN   
3                              1840.00                                NaN   
4                               966.82                                NaN   
5                              1695.00                                NaN   
6                               978.00                                NaN   
7                               996.10                                NaN   
8                               993.40                                NaN   
9                               990.80                                NaN   
10                              988.10                                NaN   
11                              985.40                                NaN   
12                              982.70                                NaN 

In [27]:
###READ SMILES INTO PYCHEM AND CREATE DATAFRAME
salts=pd.read_csv('../salty/data/salts_with_smiles.csv',delimiter=',')
salts = salts[salts.anion_name != 'chloride']  #chloride returns an error in pychem
salts = salts[salts.anion_name != 'bromide']  #bromide returns an error in pychem
salts = salts[salts.cation_name != 'ammonium']  #ammonium returns an error in pychem
salts = salts[salts.anion_name != 'trifluorotris(perfluoroethyl)phosphate(V)'] #returns an error in pychem
salts = salts[salts.anion_name != 'iodide'] #returns an error in pychem
salts = salts.reset_index()
cats = pd.DataFrame(columns=salts['cation_name']) #loop through all the salts
old = pd.DataFrame()
new = pd.DataFrame()
for a, b in enumerate(salts['cation_name']):    
    catdes=[] #descriptors for cations
    andes=[] #descriptors for anions
    cat=PyChem2d() #create PyChem molecular instances
    an=PyChem2d()
    print(b,salts['anion_SMILES'][a]) #check that we're computing
    cat.ReadMolFromSmile(np.str(salts['cation_SMILES'][a])) #cation
    an.ReadMolFromSmile(np.str(salts['anion_SMILES'][a])) #anion
    andes.append(an.GetAllDescriptor()) 
    catdes.append(cat.GetAllDescriptor()) #add all the descriptors    
    dfan = pd.DataFrame(andes) #turn the array into a dataframe
    dfcat = pd.DataFrame(catdes)
    dfan.rename(columns=lambda x: x + '-anion', inplace=True) #rename headers (cation or anion)
    dfcat.rename(columns=lambda x: x + '-cation', inplace=True)
    df = pd.concat([dfcat, dfan], axis=1) #concatonate cationic and anionic descriptor df's
    if a != 0: #grow the dataframe
        new = pd.concat([df, old], axis=0)
    old = new

1-ethyl-3-methylimidazolium C(F)(F)(F)S(=O)(=O)[N-]S(=O)(=O)C(F)(F)F
1-methyl-3-octylimidazolium [B-](F)(F)(F)F
1-hexyl-3-methylimidazolium [B-](F)(F)(F)F
1-hexyl-3-methylimidazolium [B-](F)(F)(F)F
1-ethyl-3-methylimidazolium [B-](F)(F)(F)F
1-hexyl-3-methylimidazolium C(F)(F)(F)S(=O)(=O)[N-]S(=O)(=O)C(F)(F)F
1-allyl-3-methyl-1H-imidazol-3-ium CCC(=O)[O-]
1-hexyl-3-methylimidazolium [B-](F)(F)(F)F
1-ethyl-3-methylimidazolium [B-](F)(F)(F)F
1-ethyl-3-methylimidazolium CCOS(=O)(=O)[O-]
1-ethyl-3-methylimidazolium C(F)(F)(F)S(=O)(=O)[O-]
1-ethyl-3-methylimidazolium C(F)(F)(F)S(=O)(=O)[O-]
1-ethyl-3-methylimidazolium [B-](F)(F)(F)F
trihexyl(tetradecyl)phosphonium C(F)(F)(F)S(=O)(=O)[N-]S(=O)(=O)C(F)(F)F
1-ethyl-3-methylimidazolium C(#N)[N-]C#N
1-ethyl-3-methylimidazolium [B-](F)(F)(F)F
1-ethyl-3-methylimidazolium [B-](F)(F)(F)F
1-hexyl-3-methylimidazolium [B-](F)(F)(F)F
1-hexyl-3-methylimidazolium C(F)(F)(F)S(=O)(=O)[N-]S(=O)(=O)C(F)(F)F
1-hexyl-3-methylimidazolium C(C(F)(F)S(=O)(=O)[N-]S(=

In [29]:
###Append these values in a separate step since 
###calculating the descriptors is computationally expensive

desc = new.iloc[::-1]
desc=desc.reset_index(drop=True)
desc.loc[:,'Temperature_K'] = pd.Series(salts['Temperature, K'], index=desc.index)
for a in range(len(salts['Temperature, K'])):
    desc.iloc[a-1,-1] = salts['Temperature, K'][a]
desc.loc[:,'Pressure_kPa'] = pd.Series(salts['Pressure, kPa'], index=desc.index)
for a in range(len(salts['Pressure, kPa'])):
    desc.iloc[a-1,-1] = salts['Pressure, kPa'][a]
desc.loc[:,'NAME_CAT'] = pd.Series(salts['cation_name'], index=desc.index)
for a in range(len(salts['cation_name'])):
    desc.iloc[a-1,-1] = salts['cation_name'][a]
desc.loc[:,'NAME_ANI'] = pd.Series(salts['anion_name'], index=desc.index)
for a in range(len(salts['anion_name'])):
    desc.iloc[a-1,-1] = salts['anion_name'][a]
desc.loc[:,'Density_kg/m'] = pd.Series(salts['Specific density, kg/m<SUP>3</SUP>'], index=desc.index)
for a in range(len(salts['Specific density, kg/m<SUP>3</SUP>'])):
    desc.iloc[a-1,-1] = salts['Specific density, kg/m<SUP>3</SUP>'][a]

In [30]:
pd.DataFrame.to_csv(desc, path_or_buf='../salty/data/salts_with_pychem_descriptors.csv', index=False)

<a id='check'></a>

# Check Dataset

[back to top](#top)

In [3]:
data=pd.read_csv('../salty/data/salts_with_pychem_descriptors.csv')
# data = data.loc[data["NAME_CAT"].str.contains("octyl", case=False)]
data.shape

(8653, 1271)